In [2]:
#%pip install torch==2.5.1 torchvision==0.20.1 torchaudio==2.5.1 --index-url https://download.pytorch.org/whl/cu124 --force-reinstall

In [3]:
"""import torch

def format_pytorch_version(version_str):
    # Example input: "2.0.1+cu118" -> returns "2.0.1"
    return version_str.split('+')[0]

def format_cuda_version(cuda_str):
    # If CUDA is None (CPU-only PyTorch), return "cpu"
    if cuda_str is None:
        return "cpu"
    # Example: "11.8" -> "cu118"
    return "cu" + cuda_str.replace('.', '')

TORCH_version = torch.__version__
TORCH = format_pytorch_version(TORCH_version)
CUDA_version = torch.version.cuda
CUDA = format_cuda_version(CUDA_version)

print(f"Installing packages for torch-{TORCH}+{CUDA}...")

%pip install --upgrade --no-cache-dir pyg_lib torch_scatter torch_sparse torch_cluster torch_spline_conv -f https://data.pyg.org/whl/torch-{TORCH}+{CUDA}.html

%pip install torch_geometric"""

'import torch\n\ndef format_pytorch_version(version_str):\n    # Example input: "2.0.1+cu118" -> returns "2.0.1"\n    return version_str.split(\'+\')[0]\n\ndef format_cuda_version(cuda_str):\n    # If CUDA is None (CPU-only PyTorch), return "cpu"\n    if cuda_str is None:\n        return "cpu"\n    # Example: "11.8" -> "cu118"\n    return "cu" + cuda_str.replace(\'.\', \'\')\n\nTORCH_version = torch.__version__\nTORCH = format_pytorch_version(TORCH_version)\nCUDA_version = torch.version.cuda\nCUDA = format_cuda_version(CUDA_version)\n\nprint(f"Installing packages for torch-{TORCH}+{CUDA}...")\n\n%pip install --upgrade --no-cache-dir pyg_lib torch_scatter torch_sparse torch_cluster torch_spline_conv -f https://data.pyg.org/whl/torch-{TORCH}+{CUDA}.html\n\n%pip install torch_geometric'

In [4]:
#%pip install scikit-learn imbalanced-learn xgboost

In [5]:
#%pip install optuna

### Hyperparameter Optimization Citeseer
#### SCAR 

In [3]:
from train_NNIF_GNN import run_nnif_gnn_experiment
import optuna
from typing import Dict, Any

def objective(trial: optuna.trial.Trial) -> float:
    """
    Objective function for hyperparameter optimization using Optuna.
    It builds a parameter dictionary, calls the experiment function, and
    returns the average F1 score.
    """
    params: Dict[str, Any] = {
        "dataset_name": "citeseer",      
        "mechanism": "SCAR",
        "train_pct": 0.5,
        "K": trial.suggest_int("K", 2, 9),
        "layers": trial.suggest_int("layers", 1, 2),
        "hidden_channels": trial.suggest_categorical("hidden_channels", [64,128, 256]),
        "out_channels": trial.suggest_categorical("out_channels", [64,128, 256]),
        "norm": None,
        "dropout": 0,
        "ratio": trial.suggest_float("ratio", 0.09, 0.18),
        "aggregation": 'mean',
        "treatment": "removal",#trial.suggest_categorical("treatment", ["removal", "relabeling"]),
        "model_type": trial.suggest_categorical("model_type", ['GCNConv', 'GATConv']),
        "rate_pairs": trial.suggest_int("rate_pairs", 1, 15),
        "batch_size": trial.suggest_categorical("batch_size", [128,256, 512, 1024]),
        "lr": trial.suggest_float("lr", 1e-4, 1e-2),
        "anomaly_detector":"nearest_neighbors",#trial.suggest_categorical("anomaly_detector",["nearest_neighbors","unweighted"]),
        "seeds": 5,
        "output_csv": "citeseer_scar_sampling_nnif_batch_cluster.csv",
        "min":0.845,
        "clusters":100,#trial.suggest_categorical("clusters", [50,100,200,300,400]),          
        "num_epochs":100,         
        "sampling":"sage",#trial.suggest_categorical("sampling",["sage","cluster","shine"]),         
        
    }
    
    avg_f1, std_f1 = run_nnif_gnn_experiment(params)
    
    # We aim to maximize F1 score.
    return avg_f1

# Create an Optuna study to maximize the F1 score.
study = optuna.create_study(direction="maximize")
study.optimize(objective, n_trials=200)

# Print out the best hyperparameters and corresponding F1 score.
print("Best trial:")
trial = study.best_trial
print("  Average F1:", trial.value)
print("  Best parameters:")
for key, value in trial.params.items():
    print(f"    {key}: {value}")


[I 2025-04-05 21:26:55,694] A new study created in memory with name: no-name-2dc54f90-1c17-4d6e-af2a-f0997b3cd97e


Running experiment with seed=654:
 - K=5, layers=1, hidden=128, out=256
 - norm=None, dropout=0, batch_size=512, methodology=ours
 - ratio=0.16636498241035705, aggregation=mean, treatment=removal, anomaly_detector=nearest_neighbors, sampling=sage
 - model_type=GCNConv, rate_pairs=3, clusters=100, lr=0.0032214618048342883
Epoch 0 / 100, Loss: 6.5552
Epoch 10 / 100, Loss: 5.9386
Epoch 20 / 100, Loss: 5.1447
Epoch 30 / 100, Loss: 4.7378
Epoch 40 / 100, Loss: 4.0750
Epoch 50 / 100, Loss: 3.4497
Epoch 60 / 100, Loss: 3.0148
Epoch 70 / 100, Loss: 2.5877
Epoch 80 / 100, Loss: 2.2440
Epoch 90 / 100, Loss: 1.9517
 - Metrics: Accuracy=0.9405, F1=0.8627, Recall=0.8873, Precision=0.8394
Running experiment with seed=114:
 - K=5, layers=1, hidden=128, out=256
 - norm=None, dropout=0, batch_size=512, methodology=ours
 - ratio=0.16636498241035705, aggregation=mean, treatment=removal, anomaly_detector=nearest_neighbors, sampling=sage
 - model_type=GCNConv, rate_pairs=3, clusters=100, lr=0.0032214618048

[I 2025-04-05 21:32:06,304] Trial 0 finished with value: 0.8619500117419128 and parameters: {'K': 5, 'layers': 1, 'hidden_channels': 128, 'out_channels': 256, 'ratio': 0.16636498241035705, 'model_type': 'GCNConv', 'rate_pairs': 3, 'batch_size': 512, 'lr': 0.0032214618048342883}. Best is trial 0 with value: 0.8619500117419128.


 - Metrics: Accuracy=0.9429, F1=0.8669, Recall=0.8830, Precision=0.8514
Done. Results written to citeseer_experimentations\citeseer_scar_sampling_nnif_batch_cluster_0504212655.csv.
Average F1 over valid seeds: 0.8620 ± 0.0028
Running experiment with seed=654:
 - K=3, layers=1, hidden=256, out=64
 - norm=None, dropout=0, batch_size=128, methodology=ours
 - ratio=0.10168879665371841, aggregation=mean, treatment=removal, anomaly_detector=nearest_neighbors, sampling=sage
 - model_type=GATConv, rate_pairs=2, clusters=100, lr=0.007858464378010724
Epoch 0 / 100, Loss: 18.9953
Epoch 10 / 100, Loss: 5.0904
Epoch 20 / 100, Loss: 2.1109
Epoch 30 / 100, Loss: 1.1719
Epoch 40 / 100, Loss: 0.7440
Epoch 50 / 100, Loss: 0.5101
Epoch 60 / 100, Loss: 0.3692
Epoch 70 / 100, Loss: 0.2879
Epoch 80 / 100, Loss: 0.2202
Epoch 90 / 100, Loss: 0.1764


[I 2025-04-05 21:34:09,288] Trial 1 finished with value: 0.821917808219178 and parameters: {'K': 3, 'layers': 1, 'hidden_channels': 256, 'out_channels': 64, 'ratio': 0.10168879665371841, 'model_type': 'GATConv', 'rate_pairs': 2, 'batch_size': 128, 'lr': 0.007858464378010724}. Best is trial 0 with value: 0.8619500117419128.


...

 - Metrics: Accuracy=0.9426, F1=0.8625, Recall=0.8545, Precision=0.8706
Done. Results written to citeseer_experimentations\citeseer_scar_sampling_nnif_batch_cluster_0604222354.csv.
Average F1 over valid seeds: 0.8684 ± 0.0048
Running experiment with seed=654:
 - K=3, layers=1, hidden=64, out=256
 - norm=None, dropout=0, batch_size=512, methodology=ours
 - ratio=0.13414070111551937, aggregation=mean, treatment=removal, anomaly_detector=nearest_neighbors, sampling=sage
 - model_type=GATConv, rate_pairs=12, clusters=100, lr=0.004077869698261489
Epoch 0 / 100, Loss: 5.1022
Epoch 10 / 100, Loss: 4.2240
Epoch 20 / 100, Loss: 3.4351
Epoch 30 / 100, Loss: 2.9331
Epoch 40 / 100, Loss: 2.3795
Epoch 50 / 100, Loss: 1.9347
Epoch 60 / 100, Loss: 1.6478
Epoch 70 / 100, Loss: 1.3870
Epoch 80 / 100, Loss: 1.1903
Epoch 90 / 100, Loss: 1.0267
 - Metrics: Accuracy=0.9429, F1=0.8643, Recall=0.8631, Precision=0.8655
Running experiment with seed=114:
 - K=3, layers=1, hidden=64, out=256
 - norm=None, dropou

[I 2025-04-06 22:40:28,509] Trial 198 finished with value: 0.8651951046477426 and parameters: {'K': 3, 'layers': 1, 'hidden_channels': 64, 'out_channels': 256, 'ratio': 0.13414070111551937, 'model_type': 'GATConv', 'rate_pairs': 12, 'batch_size': 512, 'lr': 0.004077869698261489}. Best is trial 191 with value: 0.8706727966697233.


 - Metrics: Accuracy=0.9408, F1=0.8584, Recall=0.8516, Precision=0.8652
Done. Results written to citeseer_experimentations\citeseer_scar_sampling_nnif_batch_cluster_0604223210.csv.
Average F1 over valid seeds: 0.8652 ± 0.0051
Running experiment with seed=654:
 - K=3, layers=1, hidden=64, out=256
 - norm=None, dropout=0, batch_size=512, methodology=ours
 - ratio=0.1307154069335918, aggregation=mean, treatment=removal, anomaly_detector=nearest_neighbors, sampling=sage
 - model_type=GATConv, rate_pairs=12, clusters=100, lr=0.004824025836874085
Epoch 0 / 100, Loss: 5.0904
Epoch 10 / 100, Loss: 4.0875
Epoch 20 / 100, Loss: 3.2031
Epoch 30 / 100, Loss: 2.6309
Epoch 40 / 100, Loss: 2.0641
Epoch 50 / 100, Loss: 1.6336
Epoch 60 / 100, Loss: 1.3651
Epoch 70 / 100, Loss: 1.1307
Epoch 80 / 100, Loss: 0.9592
Epoch 90 / 100, Loss: 0.8197
 - Metrics: Accuracy=0.9453, F1=0.8694, Recall=0.8645, Precision=0.8745
Running experiment with seed=114:
 - K=3, layers=1, hidden=64, out=256
 - norm=None, dropout

[I 2025-04-06 22:48:48,237] Trial 199 finished with value: 0.8679397578111526 and parameters: {'K': 3, 'layers': 1, 'hidden_channels': 64, 'out_channels': 256, 'ratio': 0.1307154069335918, 'model_type': 'GATConv', 'rate_pairs': 12, 'batch_size': 512, 'lr': 0.004824025836874085}. Best is trial 191 with value: 0.8706727966697233.


 - Metrics: Accuracy=0.9441, F1=0.8662, Recall=0.8588, Precision=0.8737
Done. Results written to citeseer_experimentations\citeseer_scar_sampling_nnif_batch_cluster_0604224028.csv.
Average F1 over valid seeds: 0.8679 ± 0.0034
Best trial:
  Average F1: 0.8706727966697233
  Best parameters:
    K: 3
    layers: 1
    hidden_channels: 64
    out_channels: 256
    ratio: 0.13399967308188074
    model_type: GATConv
    rate_pairs: 11
    batch_size: 512
    lr: 0.00442634047825323


### Hyperparameter Optimization Citeseer
#### SAR 

In [ ]:
from train_NNIF_GNN import run_nnif_gnn_experiment
import optuna
from typing import Dict, Any

def objective(trial: optuna.trial.Trial) -> float:
    """
    Objective function for hyperparameter optimization using Optuna.
    It builds a parameter dictionary, calls the experiment function, and
    returns the average F1 score.
    """
    params: Dict[str, Any] = {
        "dataset_name": "citeseer",      
        "mechanism": "SAR",
        "train_pct": 0.5,
        "K": trial.suggest_int("K", 2, 7),
        "layers": trial.suggest_int("layers", 1, 2),
        "hidden_channels": trial.suggest_categorical("hidden_channels", [64,128, 256]),
        "out_channels": trial.suggest_categorical("out_channels", [64,128, 256]),
        "norm": None,
        "dropout": 0,
        "ratio": trial.suggest_float("ratio", 0.09, 0.18),
        "aggregation": 'mean',
        "treatment": "removal",#trial.suggest_categorical("treatment", ["removal", "relabeling"]),
        "model_type": trial.suggest_categorical("model_type", ['GCNConv', 'GATConv']),
        "rate_pairs":trial.suggest_int("layers", 1, 15),
        "batch_size": trial.suggest_categorical("batch_size", [256,512,1024]),
        "lr": trial.suggest_float("lr", 1e-4, 1e-2),
        "anomaly_detector":trial.suggest_categorical("anomaly_detector",["nearest_neighbors","unweighted"]),
        "seeds": 5,
        "output_csv": "citeseer_sar_sampling_nnif_batch_cluster.csv",
        "min":0.845,
        "clusters":trial.suggest_categorical("clusters", [50,100,200,300,400]),
        "num_epochs":100,         
        "sampling":trial.suggest_categorical("sampling",["sage","cluster","shine"]),         
        
       
    }
    
    avg_f1, std_f1 = run_nnif_gnn_experiment(params)
    
    # We aim to maximize F1 score.
    return avg_f1

# Create an Optuna study to maximize the F1 score.
study = optuna.create_study(direction="maximize")
study.optimize(objective, n_trials=200)

# Print out the best hyperparameters and corresponding F1 score.
print("Best trial:")
trial = study.best_trial
print("  Average F1:", trial.value)
print("  Best parameters:")
for key, value in trial.params.items():
    print(f"    {key}: {value}")


[I 2025-03-25 10:10:43,640] A new study created in memory with name: no-name-f25fde7d-ee4a-4fa2-be4f-f9e486b8970e


Running experiment with seed=654:
 - K=3, layers=1, hidden=256, out=256
 - norm=None, dropout=0, batch_size=1024, methodology=ours
 - ratio=0.11307195638376069, aggregation=mean, treatment=removal, anomaly_detector=nearest_neighbors, sampling=neighbor, sampling_k=75
 - model_type=GATConv, rate_pairs=1, clusters=50, lr=0.0023234250431828636
Epoch 0 / 100, Loss: 2.8385
Epoch 10 / 100, Loss: 2.4108
Epoch 20 / 100, Loss: 2.2628
Epoch 30 / 100, Loss: 2.1825
Epoch 40 / 100, Loss: 2.0409
Epoch 50 / 100, Loss: 1.9945
Epoch 60 / 100, Loss: 1.8232
Epoch 70 / 100, Loss: 1.6971
Epoch 80 / 100, Loss: 1.6468
Epoch 90 / 100, Loss: 1.4848
 - Metrics: Accuracy=0.9405, F1=0.8507, Recall=0.8046, Precision=0.9024
Running experiment with seed=114:
 - K=3, layers=1, hidden=256, out=256
 - norm=None, dropout=0, batch_size=1024, methodology=ours
 - ratio=0.11307195638376069, aggregation=mean, treatment=removal, anomaly_detector=nearest_neighbors, sampling=neighbor, sampling_k=75
 - model_type=GATConv, rate_pa

[I 2025-03-25 10:13:49,885] Trial 0 finished with value: 0.857595508989174 and parameters: {'K': 3, 'layers': 1, 'hidden_channels': 256, 'out_channels': 256, 'ratio': 0.11307195638376069, 'model_type': 'GATConv', 'batch_size': 1024, 'lr': 0.0023234250431828636, 'anomaly_detector': 'nearest_neighbors', 'clusters': 50, 'num_epochs': 100, 'sampling': 'neighbor', 'sampling_k': 75}. Best is trial 0 with value: 0.857595508989174.


 - Metrics: Accuracy=0.9390, F1=0.8493, Recall=0.8160, Precision=0.8854
Done. Results written to citeseer_experimentations\citeseer_sar_sampling_nnif_batch_cluster_2503101043.csv.
Average F1 over valid seeds: 0.8576 ± 0.0077
Running experiment with seed=654:
 - K=7, layers=2, hidden=256, out=64
 - norm=None, dropout=0, batch_size=256, methodology=ours
 - ratio=0.17225386531043968, aggregation=mean, treatment=removal, anomaly_detector=unweighted, sampling=nearest_neighbors, sampling_k=25
 - model_type=GATConv, rate_pairs=2, clusters=400, lr=0.008752505664905935
Epoch 0 / 150, Loss: 42.4167
Epoch 10 / 150, Loss: 18.6557
Epoch 20 / 150, Loss: 10.0401
Epoch 30 / 150, Loss: 6.0609
Epoch 40 / 150, Loss: 4.2251
Epoch 50 / 150, Loss: 3.0423
Epoch 60 / 150, Loss: 2.2833
Epoch 70 / 150, Loss: 1.8259
Epoch 80 / 150, Loss: 1.4801
Epoch 90 / 150, Loss: 1.2157
Epoch 100 / 150, Loss: 1.0309
Epoch 110 / 150, Loss: 0.8732
Epoch 120 / 150, Loss: 0.7590
Epoch 130 / 150, Loss: 0.6525
Epoch 140 / 150, Loss

[I 2025-03-25 10:15:40,677] Trial 1 finished with value: 0.6813996316758748 and parameters: {'K': 7, 'layers': 2, 'hidden_channels': 256, 'out_channels': 64, 'ratio': 0.17225386531043968, 'model_type': 'GATConv', 'batch_size': 256, 'lr': 0.008752505664905935, 'anomaly_detector': 'unweighted', 'clusters': 400, 'num_epochs': 150, 'sampling': 'nearest_neighbors', 'sampling_k': 25}. Best is trial 0 with value: 0.857595508989174.


...

 - Metrics: Accuracy=0.9059, F1=0.7183, Recall=0.5692, Precision=0.9732
F1 = 0.72 < 0.845, skipping ...
Done. Results written to citeseer_experimentations\citeseer_sar_sampling_nnif_batch_cluster_2503140907.csv.
Average F1 over valid seeds: 0.7183 ± 0.0000
Running experiment with seed=654:
 - K=2, layers=1, hidden=256, out=256
 - norm=None, dropout=0, batch_size=1024, methodology=ours
 - ratio=0.15841141409782936, aggregation=mean, treatment=removal, anomaly_detector=nearest_neighbors, sampling=neighbor, sampling_k=25
 - model_type=GCNConv, rate_pairs=1, clusters=400, lr=0.004733199465670689
Epoch 0 / 100, Loss: 2.1699
Epoch 10 / 100, Loss: 1.6532
Epoch 20 / 100, Loss: 1.4729
Epoch 30 / 100, Loss: 1.3237
Epoch 40 / 100, Loss: 1.1338
Epoch 50 / 100, Loss: 1.0336
Epoch 60 / 100, Loss: 0.8867
Epoch 70 / 100, Loss: 0.7703
Epoch 80 / 100, Loss: 0.7087
Epoch 90 / 100, Loss: 0.6093
 - Metrics: Accuracy=0.9408, F1=0.8600, Recall=0.8631, Precision=0.8569
Running experiment with seed=114:
 - K=2

[I 2025-03-25 14:12:40,226] Trial 98 finished with value: 0.8617602498928539 and parameters: {'K': 2, 'layers': 1, 'hidden_channels': 256, 'out_channels': 256, 'ratio': 0.15841141409782936, 'model_type': 'GCNConv', 'batch_size': 1024, 'lr': 0.004733199465670689, 'anomaly_detector': 'nearest_neighbors', 'clusters': 400, 'num_epochs': 100, 'sampling': 'neighbor', 'sampling_k': 25}. Best is trial 87 with value: 0.8650138572197479.


 - Metrics: Accuracy=0.9387, F1=0.8539, Recall=0.8502, Precision=0.8576
Done. Results written to citeseer_experimentations\citeseer_sar_sampling_nnif_batch_cluster_2503140941.csv.
Average F1 over valid seeds: 0.8618 ± 0.0066
Running experiment with seed=654:
 - K=2, layers=1, hidden=256, out=256
 - norm=None, dropout=0, batch_size=1024, methodology=ours
 - ratio=0.16102039029803536, aggregation=mean, treatment=removal, anomaly_detector=nearest_neighbors, sampling=nearest_neighbors, sampling_k=25
 - model_type=GCNConv, rate_pairs=1, clusters=400, lr=0.004605584968207975
Epoch 0 / 100, Loss: 4.1609
Epoch 10 / 100, Loss: 3.4473
Epoch 20 / 100, Loss: 3.0725
Epoch 30 / 100, Loss: 2.6641
Epoch 40 / 100, Loss: 2.3129
Epoch 50 / 100, Loss: 2.1049
Epoch 60 / 100, Loss: 1.7786
Epoch 70 / 100, Loss: 1.6623
Epoch 80 / 100, Loss: 1.4632
Epoch 90 / 100, Loss: 1.3323


[I 2025-03-25 14:13:15,258] Trial 99 finished with value: 0.8429629629629629 and parameters: {'K': 2, 'layers': 1, 'hidden_channels': 256, 'out_channels': 256, 'ratio': 0.16102039029803536, 'model_type': 'GCNConv', 'batch_size': 1024, 'lr': 0.004605584968207975, 'anomaly_detector': 'nearest_neighbors', 'clusters': 400, 'num_epochs': 100, 'sampling': 'nearest_neighbors', 'sampling_k': 25}. Best is trial 87 with value: 0.8650138572197479.


 - Metrics: Accuracy=0.9363, F1=0.8430, Recall=0.8117, Precision=0.8767
F1 = 0.84 < 0.845, skipping ...
Done. Results written to citeseer_experimentations\citeseer_sar_sampling_nnif_batch_cluster_2503141240.csv.
Average F1 over valid seeds: 0.8430 ± 0.0000
Best trial:
  Average F1: 0.8650138572197479
  Best parameters:
    K: 2
    layers: 1
    hidden_channels: 128
    out_channels: 256
    ratio: 0.1611386183555754
    model_type: GCNConv
    batch_size: 1024
    lr: 0.0063212510924867535
    anomaly_detector: nearest_neighbors
    clusters: 200
    num_epochs: 100
    sampling: neighbor
    sampling_k: 25


### Hyperparameter Optimization Cora
#### SCAR 

In [4]:
from train_NNIF_GNN import run_nnif_gnn_experiment
import optuna
from typing import Dict, Any

def objective(trial: optuna.trial.Trial) -> float:
    """
    Objective function for hyperparameter optimization using Optuna.
    It builds a parameter dictionary, calls the experiment function, and
    returns the average F1 score.
    """
    params: Dict[str, Any] = {
        "dataset_name": "cora",      
        "mechanism": "SCAR",
        "train_pct": 0.5,
        "K": trial.suggest_int("K", 1, 12),
        "layers": trial.suggest_int("layers", 1, 2),
        "hidden_channels": trial.suggest_categorical("hidden_channels", [64,128, 256]),
        "out_channels": trial.suggest_categorical("out_channels", [64,128, 256]),
        "norm": None,
        "dropout": 0,
        "ratio": trial.suggest_float("ratio", 0.16, 0.34),
        "aggregation": 'mean',
        "treatment": "removal",#trial.suggest_categorical("treatment", ["removal", "relabeling"]),
        "model_type": trial.suggest_categorical("model_type", ['GCNConv', 'GATConv']),
        "rate_pairs":trial.suggest_int("rate_pairs", 1, 15),
        "batch_size": trial.suggest_categorical("batch_size", [128,256, 512, 1024]),
        "lr": trial.suggest_float("lr", 1e-4, 1e-2),
        "anomaly_detector":"nearest_neighbors",#trial.suggest_categorical("anomaly_detector",["nearest_neighbors","unweighted"]),
        "seeds": 5,
        "output_csv": "cora_scar_sampling_nnif_batch_cluster.csv",
        "min":0.85,
        "clusters":100,#trial.suggest_categorical("clusters", [50,100,200,300,400]),          
        "num_epochs":100,         
        "sampling":"sage",#trial.suggest_categorical("sampling",["sage","cluster","shine"]),         
        
    }
    
    avg_f1, std_f1 = run_nnif_gnn_experiment(params)
    
    # We aim to maximize F1 score.
    return avg_f1

# Create an Optuna study to maximize the F1 score.
study = optuna.create_study(direction="maximize")
study.optimize(objective, n_trials=200)

# Print out the best hyperparameters and corresponding F1 score.
print("Best trial:")
trial = study.best_trial
print("  Average F1:", trial.value)
print("  Best parameters:")
for key, value in trial.params.items():
    print(f"    {key}: {value}")


[I 2025-04-06 22:48:48,350] A new study created in memory with name: no-name-508e1c0e-97e5-4d4c-a3b0-c70d6aed68c3


Running experiment with seed=654:
 - K=11, layers=2, hidden=256, out=128
 - norm=None, dropout=0, batch_size=512, methodology=ours
 - ratio=0.1710016359498579, aggregation=mean, treatment=removal, anomaly_detector=nearest_neighbors, sampling=sage
 - model_type=GATConv, rate_pairs=14, clusters=100, lr=0.008930043676025998
Epoch 0 / 100, Loss: 8.0538
Epoch 10 / 100, Loss: 6.9068
Epoch 20 / 100, Loss: 5.3855
Epoch 30 / 100, Loss: 3.6867
Epoch 40 / 100, Loss: 2.4142
Epoch 50 / 100, Loss: 1.7237
Epoch 60 / 100, Loss: 1.2418
Epoch 70 / 100, Loss: 0.9715
Epoch 80 / 100, Loss: 0.7719
Epoch 90 / 100, Loss: 0.6375
 - Metrics: Accuracy=0.9321, F1=0.8807, Recall=0.8301, Precision=0.9378
Running experiment with seed=114:
 - K=11, layers=2, hidden=256, out=128
 - norm=None, dropout=0, batch_size=512, methodology=ours
 - ratio=0.1710016359498579, aggregation=mean, treatment=removal, anomaly_detector=nearest_neighbors, sampling=sage
 - model_type=GATConv, rate_pairs=14, clusters=100, lr=0.008930043676

[I 2025-04-06 22:56:18,934] Trial 0 finished with value: 0.8770317949658233 and parameters: {'K': 11, 'layers': 2, 'hidden_channels': 256, 'out_channels': 128, 'ratio': 0.1710016359498579, 'model_type': 'GATConv', 'rate_pairs': 14, 'batch_size': 512, 'lr': 0.008930043676025998}. Best is trial 0 with value: 0.8770317949658233.


 - Metrics: Accuracy=0.9258, F1=0.8675, Recall=0.8044, Precision=0.9413
Done. Results written to cora_experimentations\cora_scar_sampling_nnif_batch_cluster_0604224848.csv.
Average F1 over valid seeds: 0.8770 ± 0.0085
Running experiment with seed=654:
 - K=1, layers=2, hidden=128, out=64
 - norm=None, dropout=0, batch_size=256, methodology=ours
 - ratio=0.2857011742443103, aggregation=mean, treatment=removal, anomaly_detector=nearest_neighbors, sampling=sage
 - model_type=GCNConv, rate_pairs=5, clusters=100, lr=0.005195548780180935
Epoch 0 / 100, Loss: 3.7938
Epoch 10 / 100, Loss: 2.3355
Epoch 20 / 100, Loss: 1.5922
Epoch 30 / 100, Loss: 1.1318
Epoch 40 / 100, Loss: 0.8440
Epoch 50 / 100, Loss: 0.6517
Epoch 60 / 100, Loss: 0.5315
Epoch 70 / 100, Loss: 0.4325
Epoch 80 / 100, Loss: 0.3545
Epoch 90 / 100, Loss: 0.3012


[I 2025-04-06 22:58:13,234] Trial 1 finished with value: 0.8495788206979543 and parameters: {'K': 1, 'layers': 2, 'hidden_channels': 128, 'out_channels': 64, 'ratio': 0.2857011742443103, 'model_type': 'GCNConv', 'rate_pairs': 5, 'batch_size': 256, 'lr': 0.005195548780180935}. Best is trial 0 with value: 0.8770317949658233.


...

 - Metrics: Accuracy=0.9498, F1=0.9186, Recall=0.9377, Precision=0.9002
Done. Results written to cora_experimentations\cora_scar_sampling_nnif_batch_cluster_0804072057.csv.
Average F1 over valid seeds: 0.9128 ± 0.0069
Running experiment with seed=654:
 - K=4, layers=1, hidden=128, out=256
 - norm=None, dropout=0, batch_size=1024, methodology=ours
 - ratio=0.21922844068889008, aggregation=mean, treatment=removal, anomaly_detector=nearest_neighbors, sampling=sage
 - model_type=GATConv, rate_pairs=2, clusters=100, lr=0.004242375355379131
Epoch 0 / 100, Loss: 2.7537
Epoch 10 / 100, Loss: 2.3517
Epoch 20 / 100, Loss: 2.2399
Epoch 30 / 100, Loss: 2.1003
Epoch 40 / 100, Loss: 1.9162
Epoch 50 / 100, Loss: 1.8019
Epoch 60 / 100, Loss: 1.6599
Epoch 70 / 100, Loss: 1.5117
Epoch 80 / 100, Loss: 1.4022
Epoch 90 / 100, Loss: 1.2718
 - Metrics: Accuracy=0.9442, F1=0.9066, Recall=0.8961, Precision=0.9174
Running experiment with seed=114:
 - K=4, layers=1, hidden=128, out=256
 - norm=None, dropout=0, b

[I 2025-04-08 07:34:46,679] Trial 198 finished with value: 0.9003026293765863 and parameters: {'K': 4, 'layers': 1, 'hidden_channels': 128, 'out_channels': 256, 'ratio': 0.21922844068889008, 'model_type': 'GATConv', 'rate_pairs': 2, 'batch_size': 1024, 'lr': 0.004242375355379131}. Best is trial 184 with value: 0.9154820747058616.


 - Metrics: Accuracy=0.9402, F1=0.9010, Recall=0.9010, Precision=0.9010
Done. Results written to cora_experimentations\cora_scar_sampling_nnif_batch_cluster_0804073104.csv.
Average F1 over valid seeds: 0.9003 ± 0.0050
Running experiment with seed=654:
 - K=4, layers=1, hidden=128, out=256
 - norm=None, dropout=0, batch_size=256, methodology=ours
 - ratio=0.24695508183858222, aggregation=mean, treatment=removal, anomaly_detector=nearest_neighbors, sampling=sage
 - model_type=GATConv, rate_pairs=2, clusters=100, lr=0.005235418934739252
Epoch 0 / 100, Loss: 10.5500
Epoch 10 / 100, Loss: 7.4426
Epoch 20 / 100, Loss: 5.0640
Epoch 30 / 100, Loss: 3.4593
Epoch 40 / 100, Loss: 2.4747
Epoch 50 / 100, Loss: 1.8418
Epoch 60 / 100, Loss: 1.4350
Epoch 70 / 100, Loss: 1.1407
Epoch 80 / 100, Loss: 0.9470
Epoch 90 / 100, Loss: 0.7782
 - Metrics: Accuracy=0.9494, F1=0.9180, Recall=0.9377, Precision=0.8992
Running experiment with seed=114:
 - K=4, layers=1, hidden=128, out=256
 - norm=None, dropout=0, b

[I 2025-04-08 07:44:57,195] Trial 199 finished with value: 0.9133065210226331 and parameters: {'K': 4, 'layers': 1, 'hidden_channels': 128, 'out_channels': 256, 'ratio': 0.24695508183858222, 'model_type': 'GATConv', 'rate_pairs': 2, 'batch_size': 256, 'lr': 0.005235418934739252}. Best is trial 184 with value: 0.9154820747058616.


 - Metrics: Accuracy=0.9520, F1=0.9220, Recall=0.9389, Precision=0.9057
Done. Results written to cora_experimentations\cora_scar_sampling_nnif_batch_cluster_0804073446.csv.
Average F1 over valid seeds: 0.9133 ± 0.0065
Best trial:
  Average F1: 0.9154820747058616
  Best parameters:
    K: 4
    layers: 1
    hidden_channels: 128
    out_channels: 256
    ratio: 0.24253690172715467
    model_type: GATConv
    rate_pairs: 2
    batch_size: 256
    lr: 0.0050278198449980535


### Hyperparameter Optimization Cora
#### SAR 

In [ ]:
from train_NNIF_GNN import run_nnif_gnn_experiment
import optuna
from typing import Dict, Any

def objective(trial: optuna.trial.Trial) -> float:
    """
    Objective function for hyperparameter optimization using Optuna.
    It builds a parameter dictionary, calls the experiment function, and
    returns the average F1 score.
    """
    params: Dict[str, Any] = {
        "dataset_name": "cora",      
        "mechanism": "SAR",
        "train_pct": 0.5,
        "K": trial.suggest_int("K", 7, 9),
        "layers": trial.suggest_int("layers", 1, 2),
        "hidden_channels": trial.suggest_categorical("hidden_channels", [64,128, 256]),
        "out_channels": trial.suggest_categorical("out_channels", [64,128, 256]),
        "norm": None,
        "dropout": 0,
        "ratio": trial.suggest_float("ratio", 0.16, 0.34),
        "aggregation": 'mean',
        "treatment": "removal",#trial.suggest_categorical("treatment", ["removal", "relabeling"]),
        "model_type": trial.suggest_categorical("model_type", ['GCNConv', 'GATConv']),
        "rate_pairs":trial.suggest_int("rate_pairs", 1, 15),
        "batch_size": trial.suggest_categorical("batch_size", [5,10,15]),
        "lr": trial.suggest_float("lr", 1e-4, 1e-2),
        "anomaly_detector":trial.suggest_categorical("anomaly_detector",["nearest_neighbors","unweighted"]),
        "seeds": 5,
        "output_csv": "cora_sar_sampling_nnif_batch_cluster.csv",
        "min":0.85,
        "clusters":trial.suggest_categorical("clusters", [50,100,200,300,400]),          
        "num_epochs":trial.suggest_categorical("num_epochs", [50,100,150]),         
        "sampling":"cluster",#trial.suggest_categorical("sampling",["sage","cluster","shine"]),         
        
       
    }
    
    avg_f1, std_f1 = run_nnif_gnn_experiment(params)
    
    # We aim to maximize F1 score.
    return avg_f1

# Create an Optuna study to maximize the F1 score.
study = optuna.create_study(direction="maximize")
study.optimize(objective, n_trials=100)

# Print out the best hyperparameters and corresponding F1 score.
print("Best trial:")
trial = study.best_trial
print("  Average F1:", trial.value)
print("  Best parameters:")
for key, value in trial.params.items():
    print(f"    {key}: {value}")


[I 2025-03-26 15:51:16,342] A new study created in memory with name: no-name-8176da62-abb1-46e4-8807-5e5ff1459ce0


Running experiment with seed=654:
 - K=9, layers=1, hidden=64, out=256
 - norm=None, dropout=0, batch_size=1024, methodology=ours
 - ratio=0.16889523261113468, aggregation=mean, treatment=removal, anomaly_detector=nearest_neighbors, sampling=neighbor, sampling_k=75
 - model_type=GCNConv, rate_pairs=1, clusters=400, lr=0.007646163484926425
Epoch 0 / 150, Loss: 3.4303
Epoch 10 / 150, Loss: 3.1501
Epoch 20 / 150, Loss: 2.8808
Epoch 30 / 150, Loss: 2.6330
Epoch 40 / 150, Loss: 2.3545
Epoch 50 / 150, Loss: 2.0481
Epoch 60 / 150, Loss: 1.7211
Epoch 70 / 150, Loss: 1.4545
Epoch 80 / 150, Loss: 1.2300
Epoch 90 / 150, Loss: 1.0373
Epoch 100 / 150, Loss: 0.8788
Epoch 110 / 150, Loss: 0.7530
Epoch 120 / 150, Loss: 0.6579
Epoch 130 / 150, Loss: 0.5790
Epoch 140 / 150, Loss: 0.5190
 - Metrics: Accuracy=0.9228, F1=0.8656, Recall=0.8227, Precision=0.9132
Running experiment with seed=114:
 - K=9, layers=1, hidden=64, out=256
 - norm=None, dropout=0, batch_size=1024, methodology=ours
 - ratio=0.1688952

[I 2025-03-26 15:53:50,635] Trial 0 finished with value: 0.8684716037566916 and parameters: {'K': 9, 'layers': 1, 'hidden_channels': 64, 'out_channels': 256, 'ratio': 0.16889523261113468, 'model_type': 'GCNConv', 'batch_size': 1024, 'lr': 0.007646163484926425, 'anomaly_detector': 'nearest_neighbors', 'clusters': 400, 'num_epochs': 150, 'sampling': 'neighbor', 'sampling_k': 75}. Best is trial 0 with value: 0.8684716037566916.


 - Metrics: Accuracy=0.9269, F1=0.8731, Recall=0.8325, Precision=0.9178
Done. Results written to cora_experimentations\cora_sar_sampling_nnif_batch_cluster_2603155116.csv.
Average F1 over valid seeds: 0.8685 ± 0.0049
Running experiment with seed=654:
 - K=9, layers=1, hidden=128, out=256
 - norm=None, dropout=0, batch_size=512, methodology=ours
 - ratio=0.1886114414198443, aggregation=mean, treatment=removal, anomaly_detector=unweighted, sampling=nearest_neighbors, sampling_k=25
 - model_type=GCNConv, rate_pairs=1, clusters=200, lr=0.00016096248213070527
Epoch 0 / 150, Loss: 35.3035
Epoch 10 / 150, Loss: 35.6685
Epoch 20 / 150, Loss: 34.8467
Epoch 30 / 150, Loss: 34.7338
Epoch 40 / 150, Loss: 34.8928
Epoch 50 / 150, Loss: 34.1160
Epoch 60 / 150, Loss: 33.9046
Epoch 70 / 150, Loss: 33.9726
Epoch 80 / 150, Loss: 33.1283
Epoch 90 / 150, Loss: 33.2420
Epoch 100 / 150, Loss: 32.6670
Epoch 110 / 150, Loss: 32.7155
[Early Stopping] at epoch 118


[I 2025-03-26 15:54:30,723] Trial 1 finished with value: 0.6825775656324582 and parameters: {'K': 9, 'layers': 1, 'hidden_channels': 128, 'out_channels': 256, 'ratio': 0.1886114414198443, 'model_type': 'GCNConv', 'batch_size': 512, 'lr': 0.00016096248213070527, 'anomaly_detector': 'unweighted', 'clusters': 200, 'num_epochs': 150, 'sampling': 'nearest_neighbors', 'sampling_k': 25}. Best is trial 0 with value: 0.8684716037566916.


...

Epoch 0 / 100, Loss: 5.9769
Epoch 10 / 100, Loss: 5.1580
Epoch 20 / 100, Loss: 4.5073
Epoch 30 / 100, Loss: 3.6713
Epoch 40 / 100, Loss: 3.1895
Epoch 50 / 100, Loss: 2.3100
Epoch 60 / 100, Loss: 1.8741
Epoch 70 / 100, Loss: 1.5376
Epoch 80 / 100, Loss: 1.2265
Epoch 90 / 100, Loss: 1.0520
 - Metrics: Accuracy=0.9210, F1=0.8694, Recall=0.8704, Precision=0.8683
Running experiment with seed=25:
 - K=8, layers=1, hidden=128, out=256
 - norm=None, dropout=0, batch_size=1024, methodology=ours
 - ratio=0.2573033125681119, aggregation=mean, treatment=removal, anomaly_detector=nearest_neighbors, sampling=cluster, sampling_k=25
 - model_type=GCNConv, rate_pairs=1, clusters=100, lr=0.007397697366787508


Computing METIS partitioning...
Done!


Epoch 0 / 100, Loss: 5.8094


[W 2025-03-26 16:49:22,637] Trial 31 failed with parameters: {'K': 8, 'layers': 1, 'hidden_channels': 128, 'out_channels': 256, 'ratio': 0.2573033125681119, 'model_type': 'GCNConv', 'batch_size': 1024, 'lr': 0.007397697366787508, 'anomaly_detector': 'nearest_neighbors', 'clusters': 100, 'num_epochs': 100, 'sampling': 'cluster', 'sampling_k': 25} because of the following error: KeyboardInterrupt().
Traceback (most recent call last):
  File "c:\Users\romai\Desktop\gnn\gnn_pu\.conda\Lib\site-packages\optuna\study\_optimize.py", line 197, in _run_trial
    value_or_values = func(trial)
                      ^^^^^^^^^^^
  File "C:\Users\romai\AppData\Local\Temp\ipykernel_39988\45902056.py", line 39, in objective
    avg_f1, std_f1 = run_nnif_gnn_experiment(params)
                     ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "c:\Users\romai\Desktop\gnn\gnn_pu\NNIF-GNN\train_NNIF_GNN.py", line 565, in run_nnif_gnn_experiment
    train_labels, train_proba, train_losses = train_graph(
          

KeyboardInterrupt: 

### Hyperparameter Optimization Pubmed
#### SCAR 

In [ ]:
from train_NNIF_GNN import run_nnif_gnn_experiment
import optuna
from typing import Dict, Any

def objective(trial: optuna.trial.Trial) -> float:
    """
    Objective function for hyperparameter optimization using Optuna.
    It builds a parameter dictionary, calls the experiment function, and
    returns the average F1 score.
    """
    params: Dict[str, Any] = {
        "dataset_name": "pubmed",      
        "mechanism": "SCAR",
        "train_pct": 0.5,
        "K": trial.suggest_int("K", 2, 20),
        "layers": trial.suggest_int("layers", 1, 2),
        "hidden_channels": trial.suggest_categorical("hidden_channels", [64,128, 256]),
        "out_channels": trial.suggest_categorical("out_channels", [64,128, 256]),
        "norm": None,
        "dropout": 0,
        "ratio": trial.suggest_float("ratio", 0.2, 0.4),
        "aggregation": 'mean',
        "treatment": "removal",#trial.suggest_categorical("treatment", ["removal", "relabeling"]),
        "model_type": trial.suggest_categorical("model_type", ['GCNConv', 'GATConv']),
        "rate_pairs":trial.suggest_int("rate_pairs", 1, 15),
        "batch_size": trial.suggest_categorical("batch_size", [128,256, 512, 1024]),
        "lr": trial.suggest_float("lr", 1e-4, 1e-2),
        "anomaly_detector": "nearest_neighbors",#trial.suggest_categorical("anomaly_detector",["nearest_neighbors","unweighted"]),
        "seeds": 2,
        "output_csv": "pubmed_scar_sampling_nnif_batch_cluster.csv",
        "min":0.84,
        "clusters":100,#trial.suggest_categorical("clusters", [50,100,200,300,400]),          
        "num_epochs":100,         
        "sampling":"sage",#trial.suggest_categorical("sampling",["sage","cluster","shine"]),         
    }
    
    avg_f1, std_f1 = run_nnif_gnn_experiment(params)
    
    # We aim to maximize F1 score.
    return avg_f1

# Create an Optuna study to maximize the F1 score.
study = optuna.create_study(direction="maximize")
study.optimize(objective, n_trials=200)

# Print out the best hyperparameters and corresponding F1 score.
print("Best trial:")
trial = study.best_trial
print("  Average F1:", trial.value)
print("  Best parameters:")
for key, value in trial.params.items():
    print(f"    {key}: {value}")


[I 2025-04-08 07:44:57,251] A new study created in memory with name: no-name-b5664c59-9526-430b-910b-198fbec8660f


Running experiment with seed=654:
 - K=8, layers=2, hidden=256, out=64
 - norm=None, dropout=0, batch_size=256, methodology=ours
 - ratio=0.3149678277472744, aggregation=mean, treatment=removal, anomaly_detector=nearest_neighbors, sampling=sage
 - model_type=GCNConv, rate_pairs=13, clusters=100, lr=0.005346285973835613
Epoch 0 / 100, Loss: 118.7781
Epoch 10 / 100, Loss: 13.1227
Epoch 20 / 100, Loss: 4.2340
Epoch 30 / 100, Loss: 2.0100
Epoch 40 / 100, Loss: 1.1163
Epoch 50 / 100, Loss: 0.6661
Epoch 60 / 100, Loss: 0.4170
Epoch 70 / 100, Loss: 0.2691
Epoch 80 / 100, Loss: 0.1780
Epoch 90 / 100, Loss: 0.1185
 - Metrics: Accuracy=0.8864, F1=0.8573, Recall=0.8542, Precision=0.8605
Running experiment with seed=114:
 - K=8, layers=2, hidden=256, out=64
 - norm=None, dropout=0, batch_size=256, methodology=ours
 - ratio=0.3149678277472744, aggregation=mean, treatment=removal, anomaly_detector=nearest_neighbors, sampling=sage
 - model_type=GCNConv, rate_pairs=13, clusters=100, lr=0.0053462859738

[I 2025-04-08 08:24:36,355] Trial 0 finished with value: 0.8399366221955363 and parameters: {'K': 8, 'layers': 2, 'hidden_channels': 256, 'out_channels': 64, 'ratio': 0.3149678277472744, 'model_type': 'GCNConv', 'rate_pairs': 13, 'batch_size': 256, 'lr': 0.005346285973835613}. Best is trial 0 with value: 0.8399366221955363.


 - Metrics: Accuracy=0.8608, F1=0.8225, Recall=0.8079, Precision=0.8378
F1 = 0.82 < 0.84, skipping ...
Done. Results written to pubmed_experimentations\pubmed_scar_sampling_nnif_batch_cluster_0804074457.csv.
Average F1 over valid seeds: 0.8399 ± 0.0174
Running experiment with seed=654:
 - K=6, layers=2, hidden=64, out=256
 - norm=None, dropout=0, batch_size=512, methodology=ours
 - ratio=0.21404214411111533, aggregation=mean, treatment=removal, anomaly_detector=nearest_neighbors, sampling=sage
 - model_type=GATConv, rate_pairs=10, clusters=100, lr=0.005668039050939195
Epoch 0 / 100, Loss: 49.7337
Epoch 10 / 100, Loss: 12.7254
Epoch 20 / 100, Loss: 4.7721
Epoch 30 / 100, Loss: 2.5103
Epoch 40 / 100, Loss: 1.5452
Epoch 50 / 100, Loss: 1.0366
Epoch 60 / 100, Loss: 0.7345
Epoch 70 / 100, Loss: 0.5378
Epoch 80 / 100, Loss: 0.4076
Epoch 90 / 100, Loss: 0.3142
 - Metrics: Accuracy=0.8913, F1=0.8535, Recall=0.7924, Precision=0.9247
Running experiment with seed=114:
 - K=6, layers=2, hidden=64,

[I 2025-04-08 08:49:14,054] Trial 1 finished with value: 0.8550049650940639 and parameters: {'K': 6, 'layers': 2, 'hidden_channels': 64, 'out_channels': 256, 'ratio': 0.21404214411111533, 'model_type': 'GATConv', 'rate_pairs': 10, 'batch_size': 512, 'lr': 0.005668039050939195}. Best is trial 1 with value: 0.8550049650940639.


...

 - Metrics: Accuracy=0.9026, F1=0.8751, Recall=0.8543, Precision=0.8968
Done. Results written to pubmed_experimentations\pubmed_scar_sampling_nnif_batch_cluster_1004092943.csv.
Average F1 over valid seeds: 0.8723 ± 0.0028
Running experiment with seed=654:
 - K=4, layers=2, hidden=128, out=64
 - norm=None, dropout=0, batch_size=128, methodology=ours
 - ratio=0.2731354959956906, aggregation=mean, treatment=removal, anomaly_detector=nearest_neighbors, sampling=sage
 - model_type=GATConv, rate_pairs=7, clusters=100, lr=0.007109394512361101
Epoch 0 / 100, Loss: 125.8417
Epoch 10 / 100, Loss: 3.6252
Epoch 20 / 100, Loss: 0.9830
Epoch 30 / 100, Loss: 0.3716
Epoch 40 / 100, Loss: 0.1580
Epoch 50 / 100, Loss: 0.0703
Epoch 60 / 100, Loss: 0.0322
Epoch 70 / 100, Loss: 0.0147
Epoch 80 / 100, Loss: 0.0068
Epoch 90 / 100, Loss: 0.0031


[I 2025-04-10 10:19:42,994] Trial 129 finished with value: 0.8292231404958678 and parameters: {'K': 4, 'layers': 2, 'hidden_channels': 128, 'out_channels': 64, 'ratio': 0.2731354959956906, 'model_type': 'GATConv', 'rate_pairs': 7, 'batch_size': 128, 'lr': 0.007109394512361101}. Best is trial 87 with value: 0.877642965838467.


 - Metrics: Accuracy=0.8690, F1=0.8292, Recall=0.7963, Precision=0.8650
F1 = 0.83 < 0.84, skipping ...
Done. Results written to pubmed_experimentations\pubmed_scar_sampling_nnif_batch_cluster_1004094618.csv.
Average F1 over valid seeds: 0.8292 ± 0.0000
Running experiment with seed=654:
 - K=8, layers=2, hidden=128, out=128
 - norm=None, dropout=0, batch_size=1024, methodology=ours
 - ratio=0.23534848777981593, aggregation=mean, treatment=removal, anomaly_detector=nearest_neighbors, sampling=sage
 - model_type=GATConv, rate_pairs=5, clusters=100, lr=0.009141900502529188
Epoch 0 / 100, Loss: 29.0379
Epoch 10 / 100, Loss: 9.6823
Epoch 20 / 100, Loss: 3.6372
Epoch 30 / 100, Loss: 1.9482
Epoch 40 / 100, Loss: 1.2286
Epoch 50 / 100, Loss: 0.8580
Epoch 60 / 100, Loss: 0.6307
Epoch 70 / 100, Loss: 0.4849
Epoch 80 / 100, Loss: 0.3815
Epoch 90 / 100, Loss: 0.3092
 - Metrics: Accuracy=0.9015, F1=0.8731, Recall=0.8483, Precision=0.8994
Running experiment with seed=114:
 - K=8, layers=2, hidden=128

[I 2025-04-10 10:36:25,515] Trial 130 finished with value: 0.8744793535770208 and parameters: {'K': 8, 'layers': 2, 'hidden_channels': 128, 'out_channels': 128, 'ratio': 0.23534848777981593, 'model_type': 'GATConv', 'rate_pairs': 5, 'batch_size': 1024, 'lr': 0.009141900502529188}. Best is trial 87 with value: 0.877642965838467.


 - Metrics: Accuracy=0.9041, F1=0.8759, Recall=0.8467, Precision=0.9071
Done. Results written to pubmed_experimentations\pubmed_scar_sampling_nnif_batch_cluster_1004101943.csv.
Average F1 over valid seeds: 0.8745 ± 0.0014
Running experiment with seed=654:
 - K=7, layers=2, hidden=128, out=128
 - norm=None, dropout=0, batch_size=1024, methodology=ours
 - ratio=0.25177894718422916, aggregation=mean, treatment=removal, anomaly_detector=nearest_neighbors, sampling=sage
 - model_type=GATConv, rate_pairs=8, clusters=100, lr=0.008396200872216673
Epoch 0 / 100, Loss: 27.2867
Epoch 10 / 100, Loss: 9.8396
Epoch 20 / 100, Loss: 3.8900
Epoch 30 / 100, Loss: 2.1120
Epoch 40 / 100, Loss: 1.3389
Epoch 50 / 100, Loss: 0.9374
Epoch 60 / 100, Loss: 0.6901
Epoch 70 / 100, Loss: 0.5313
Epoch 80 / 100, Loss: 0.4181
Epoch 90 / 100, Loss: 0.3390
 - Metrics: Accuracy=0.9013, F1=0.8739, Recall=0.8565, Precision=0.8921
Running experiment with seed=114:
 - K=7, layers=2, hidden=128, out=128
 - norm=None, dropout

### Hyperparameter Optimization Pubmed
#### SAR 

In [ ]:
from train_NNIF_GNN import run_nnif_gnn_experiment
import optuna
from typing import Dict, Any

def objective(trial: optuna.trial.Trial) -> float:
    """
    Objective function for hyperparameter optimization using Optuna.
    It builds a parameter dictionary, calls the experiment function, and
    returns the average F1 score.
    """
    params: Dict[str, Any] = {
        "dataset_name": "pubmed",      
        "mechanism": "SAR",
        "train_pct": 0.5,
        "K": trial.suggest_int("K", 2, 12),
        "layers": trial.suggest_int("layers", 1, 2),
        "hidden_channels": trial.suggest_categorical("hidden_channels", [64,128, 256]),
        "out_channels": trial.suggest_categorical("out_channels", [64,128, 256]),
        "norm": None,
        "dropout": 0,
        "ratio": trial.suggest_float("ratio", 0.2, 0.4),
        "aggregation": 'mean',
        "treatment": "removal",#trial.suggest_categorical("treatment", ["removal", "relabeling"]),
        "model_type": trial.suggest_categorical("model_type", ['GCNConv', 'GATConv']),
        "rate_pairs":trial.suggest_int("layers", 1, 15),
        "batch_size": trial.suggest_categorical("batch_size", [15,256,512,1024]),
        "lr": trial.suggest_float("lr", 1e-4, 1e-2),
        "anomaly_detector":"nearest_neighbors",#trial.suggest_categorical("anomaly_detector",["nearest_neighbors","unweighted"]),
        "seeds": 5,
        "output_csv": "pubmed_sar_sampling_nnif_batch_cluster.csv",
        "min":0.84,
        "clusters":trial.suggest_categorical("clusters", [50,100,200,300,400]),          
        "num_epochs":trial.suggest_categorical("num_epochs", [50,100,150]),         
        "sampling":trial.suggest_categorical("sampling",["sage","cluster","shine"]),         
        
       
    }
    
    avg_f1, std_f1 = run_nnif_gnn_experiment(params)
    
    # We aim to maximize F1 score.
    return avg_f1

# Create an Optuna study to maximize the F1 score.
study = optuna.create_study(direction="maximize")
study.optimize(objective, n_trials=200)

# Print out the best hyperparameters and corresponding F1 score.
print("Best trial:")
trial = study.best_trial
print("  Average F1:", trial.value)
print("  Best parameters:")
for key, value in trial.params.items():
    print(f"    {key}: {value}")


[I 2025-03-24 05:51:18,349] A new study created in memory with name: no-name-7363eccd-5b06-40dc-87b0-25014df8c5a1


Running experiment with seed=654:
 - K=7, layers=2, hidden=128, out=256
 - norm=None, dropout=0, batch_size=1024, methodology=ours
 - ratio=0.3362908893186948, aggregation=mean, treatment=removal, anomaly_detector=unweighted, sampling=cluster, sampling_k=50
 - model_type=GATConv, rate_pairs=10, clusters=300, lr=0.0007087214622711031


Computing METIS partitioning...
Done!


Epoch 0 / 100, Loss: 18.5522
Epoch 10 / 100, Loss: 17.8089
Epoch 20 / 100, Loss: 17.3418
Epoch 30 / 100, Loss: 16.8934
Epoch 40 / 100, Loss: 16.1184
Epoch 50 / 100, Loss: 15.1700
Epoch 60 / 100, Loss: 14.4180
Epoch 70 / 100, Loss: 13.4842
Epoch 80 / 100, Loss: 12.6036
Epoch 90 / 100, Loss: 11.9384


[I 2025-03-24 05:53:00,820] Trial 0 finished with value: 0.715743932941256 and parameters: {'K': 7, 'ratio': 0.3362908893186948, 'model_type': 'GATConv', 'batch_size': 1024, 'lr': 0.0007087214622711031, 'anomaly_detector': 'unweighted', 'clusters': 300, 'num_epochs': 100, 'sampling': 'cluster', 'sampling_k': 50}. Best is trial 0 with value: 0.715743932941256.


...

 - Metrics: Accuracy=0.8745, F1=0.8391, Recall=0.8193, Precision=0.8598
F1 = 0.84 < 0.84, skipping ...
Done. Results written to pubmed_experimentations\pubmed_sar_sampling_nnif_batch_cluster_2403133828.csv.
Average F1 over valid seeds: 0.8391 ± 0.0000
Running experiment with seed=654:
 - K=7, layers=2, hidden=128, out=256
 - norm=None, dropout=0, batch_size=512, methodology=ours
 - ratio=0.28001597838526016, aggregation=mean, treatment=removal, anomaly_detector=nearest_neighbors, sampling=nearest_neighbors, sampling_k=50
 - model_type=GCNConv, rate_pairs=10, clusters=400, lr=0.00873922908266354
Epoch 0 / 50, Loss: 58.0806
Epoch 10 / 50, Loss: 8.0599
Epoch 20 / 50, Loss: 2.8407
Epoch 30 / 50, Loss: 1.4709
Epoch 40 / 50, Loss: 0.8989
 - Metrics: Accuracy=0.8762, F1=0.8413, Recall=0.8212, Precision=0.8624
Running experiment with seed=114:
 - K=7, layers=2, hidden=128, out=256
 - norm=None, dropout=0, batch_size=512, methodology=ours
 - ratio=0.28001597838526016, aggregation=mean, treatmen

[I 2025-03-24 15:01:39,121] Trial 13 finished with value: 0.835498509343777 and parameters: {'K': 7, 'ratio': 0.28001597838526016, 'model_type': 'GCNConv', 'batch_size': 512, 'lr': 0.00873922908266354, 'anomaly_detector': 'nearest_neighbors', 'clusters': 400, 'num_epochs': 50, 'sampling': 'nearest_neighbors', 'sampling_k': 50}. Best is trial 10 with value: 0.8395798210348853.


 - Metrics: Accuracy=0.8702, F1=0.8297, Recall=0.7916, Precision=0.8716
F1 = 0.83 < 0.84, skipping ...
Done. Results written to pubmed_experimentations\pubmed_sar_sampling_nnif_batch_cluster_2403141459.csv.
Average F1 over valid seeds: 0.8355 ± 0.0058
Running experiment with seed=654:
 - K=7, layers=2, hidden=128, out=256
 - norm=None, dropout=0, batch_size=512, methodology=ours
 - ratio=0.26308150498044675, aggregation=mean, treatment=removal, anomaly_detector=nearest_neighbors, sampling=nearest_neighbors, sampling_k=50
 - model_type=GCNConv, rate_pairs=10, clusters=400, lr=0.009817622280543212
Epoch 0 / 50, Loss: 57.2382
Epoch 10 / 50, Loss: 6.7150
Epoch 20 / 50, Loss: 2.3497


[W 2025-03-24 15:11:12,619] Trial 14 failed with parameters: {'K': 7, 'ratio': 0.26308150498044675, 'model_type': 'GCNConv', 'batch_size': 512, 'lr': 0.009817622280543212, 'anomaly_detector': 'nearest_neighbors', 'clusters': 400, 'num_epochs': 50, 'sampling': 'nearest_neighbors', 'sampling_k': 50} because of the following error: KeyboardInterrupt().
Traceback (most recent call last):
  File "c:\Users\romai\Desktop\gnn\gnn_pu\.conda\Lib\site-packages\optuna\study\_optimize.py", line 197, in _run_trial
    value_or_values = func(trial)
                      ^^^^^^^^^^^
  File "C:\Users\romai\AppData\Local\Temp\ipykernel_22248\4249684348.py", line 39, in objective
    avg_f1, std_f1 = run_nnif_gnn_experiment(params)
                     ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "c:\Users\romai\Desktop\gnn\gnn_pu\NNIF-GNN\train_NNIF_GNN.py", line 565, in run_nnif_gnn_experiment
    train_labels, train_proba, train_losses = train_graph(
                                              ^^^^^^^^^^^

KeyboardInterrupt: 

### Hyperparameter Optimization WikiCS
#### SCAR 

In [ ]:
from train_NNIF_GNN import run_nnif_gnn_experiment
import optuna
from typing import Dict, Any

def objective(trial: optuna.trial.Trial) -> float:
    """
    Objective function for hyperparameter optimization using Optuna.
    It builds a parameter dictionary, calls the experiment function, and
    returns the average F1 score.
    """
    params: Dict[str, Any] = {
        "dataset_name": "wiki-cs",      
        "mechanism": "SCAR",
        "train_pct": 0.5,
        "K": trial.suggest_int("K", 1, 35),
        "layers": trial.suggest_int("layers", 1, 2),
        "hidden_channels": trial.suggest_categorical("hidden_channels", [64,128, 256]),
        "out_channels": trial.suggest_categorical("out_channels", [64,128, 256]),
        "norm": None,
        "dropout": 0,
        "ratio": trial.suggest_float("ratio", 0.09, 0.35),
        "aggregation": 'mean',
        "treatment": "removal",#trial.suggest_categorical("treatment", ["removal", "relabeling"]),
        "model_type": trial.suggest_categorical("model_type", ['GCNConv', 'GATConv']),
        "rate_pairs":trial.suggest_int("rate_pairs",1,15),
        "batch_size": trial.suggest_categorical("batch_size", [5,10,15,20]),
        "lr": trial.suggest_float("lr", 1e-4, 1e-2),
        "anomaly_detector":"nearest_neighbors",#trial.suggest_categorical("anomaly_detector",["nearest_neighbors","unweighted"]),
        "seeds": 5,
        "output_csv": "wikics_scar_sampling_nnif_batch_cluster.csv",
        "min":0.88,
        "clusters":trial.suggest_categorical("clusters", [50,100,200,300,400]),          
        "num_epochs":100,      
        "sampling":"cluster",#trial.suggest_categorical("sampling",["sage","cluster","shine"]),         
        
       
    }
    
    avg_f1, std_f1 = run_nnif_gnn_experiment(params)
    
    # We aim to maximize F1 score.
    return avg_f1

# Create an Optuna study to maximize the F1 score.
study = optuna.create_study(direction="maximize")
study.optimize(objective, n_trials=200)

# Print out the best hyperparameters and corresponding F1 score.
print("Best trial:")
trial = study.best_trial
print("  Average F1:", trial.value)
print("  Best parameters:")
for key, value in trial.params.items():
    print(f"    {key}: {value}")


[I 2025-03-28 04:20:38,026] A new study created in memory with name: no-name-b7804c88-d9f4-4272-be1e-f766b03ffaed
Computing METIS partitioning...


Running experiment with seed=654:
 - K=11, layers=1, hidden=128, out=64
 - norm=None, dropout=0, batch_size=512, methodology=ours
 - ratio=0.1926695943076433, aggregation=mean, treatment=removal, anomaly_detector=nearest_neighbors, sampling=cluster, sampling_k=75
 - model_type=GCNConv, rate_pairs=15, clusters=100, lr=0.0025061759908526224


Done!


Epoch 0 / 100, Loss: 18.5554
Epoch 10 / 100, Loss: 17.3968
Epoch 20 / 100, Loss: 14.5902
Epoch 30 / 100, Loss: 13.5468
Epoch 40 / 100, Loss: 11.3363
Epoch 50 / 100, Loss: 10.3032
Epoch 60 / 100, Loss: 9.2580
Epoch 70 / 100, Loss: 8.0010
Epoch 80 / 100, Loss: 6.8279
Epoch 90 / 100, Loss: 5.9414
 - Metrics: Accuracy=0.9435, F1=0.8836, Recall=0.9369, Precision=0.8361
Running experiment with seed=114:
 - K=11, layers=1, hidden=128, out=64
 - norm=None, dropout=0, batch_size=512, methodology=ours
 - ratio=0.1926695943076433, aggregation=mean, treatment=removal, anomaly_detector=nearest_neighbors, sampling=cluster, sampling_k=75
 - model_type=GCNConv, rate_pairs=15, clusters=100, lr=0.0025061759908526224


Computing METIS partitioning...
Done!


...

Epoch 0 / 100, Loss: 3.5138
Epoch 10 / 100, Loss: 2.8710
Epoch 20 / 100, Loss: 2.4437
Epoch 30 / 100, Loss: 2.1170
Epoch 40 / 100, Loss: 1.7531
Epoch 50 / 100, Loss: 1.5131
Epoch 60 / 100, Loss: 1.2861
Epoch 70 / 100, Loss: 1.1255
Epoch 80 / 100, Loss: 0.9426
Epoch 90 / 100, Loss: 0.8364
 - Metrics: Accuracy=0.9606, F1=0.9140, Recall=0.9149, Precision=0.9132
Running experiment with seed=281:
 - K=5, layers=2, hidden=256, out=128
 - norm=None, dropout=0, batch_size=1024, methodology=ours
 - ratio=0.15148200168671186, aggregation=mean, treatment=removal, anomaly_detector=nearest_neighbors, sampling=cluster, sampling_k=75
 - model_type=GCNConv, rate_pairs=14, clusters=50, lr=0.008372583695812601


Computing METIS partitioning...
Done!


Epoch 0 / 100, Loss: 3.2542
Epoch 10 / 100, Loss: 3.0165
Epoch 20 / 100, Loss: 2.9101
Epoch 30 / 100, Loss: 2.1438
Epoch 40 / 100, Loss: 1.7470
Epoch 50 / 100, Loss: 1.5032
Epoch 60 / 100, Loss: 1.2463
Epoch 70 / 100, Loss: 1.2354
Epoch 80 / 100, Loss: 0.9383
Epoch 90 / 100, Loss: 0.8335


[I 2025-03-29 19:17:01,312] Trial 199 finished with value: 0.9171701172307115 and parameters: {'K': 5, 'layers': 2, 'hidden_channels': 256, 'out_channels': 128, 'ratio': 0.15148200168671186, 'model_type': 'GCNConv', 'rate_pairs': 14, 'batch_size': 1024, 'lr': 0.008372583695812601, 'clusters': 50, 'sampling': 'cluster', 'sampling_k': 75}. Best is trial 137 with value: 0.9189642012571827.


 - Metrics: Accuracy=0.9607, F1=0.9128, Recall=0.8988, Precision=0.9272
Done. Results written to wiki-cs_experimentations\wikics_scar_sampling_nnif_batch_cluster_2903191355.csv.
Average F1 over valid seeds: 0.9172 ± 0.0037
Best trial:
  Average F1: 0.9189642012571827
  Best parameters:
    K: 8
    layers: 2
    hidden_channels: 256
    out_channels: 128
    ratio: 0.16224551381027605
    model_type: GCNConv
    rate_pairs: 13
    batch_size: 512
    lr: 0.007865383500608529
    clusters: 50
    sampling: cluster
    sampling_k: 75


### Hyperparameter Optimization WikiCS
#### SAR 

In [ ]:
from train_NNIF_GNN import run_nnif_gnn_experiment
import optuna
from typing import Dict, Any

def objective(trial: optuna.trial.Trial) -> float:
    """
    Objective function for hyperparameter optimization using Optuna.
    It builds a parameter dictionary, calls the experiment function, and
    returns the average F1 score.
    """
    params: Dict[str, Any] = {
        "dataset_name": "wiki-cs",      
        "mechanism": "SAR",
        "train_pct": 0.5,
        "K": trial.suggest_int("K", 3, 40),
        "layers": trial.suggest_int("layers", 1, 2),
        "hidden_channels": trial.suggest_categorical("hidden_channels", [64,128, 256]),
        "out_channels": trial.suggest_categorical("out_channels", [64,128, 256]),
        "norm": None,
        "dropout": 0,
        "ratio": trial.suggest_float("ratio", 0.09, 0.18),
        "aggregation": 'mean',
        "treatment": "removal",#trial.suggest_categorical("treatment", ["removal", "relabeling"]),
        "model_type": trial.suggest_categorical("model_type", ['GCNConv', 'GATConv']),
        "rate_pairs":trial.suggest_int("rate_pairs",1,10),
        "batch_size": trial.suggest_categorical("batch_size", [256,512,1024]),
        "lr": trial.suggest_float("lr", 1e-4, 1e-2),
        "anomaly_detector":"nearest_neighbors",#trial.suggest_categorical("anomaly_detector",["nearest_neighbors","unweighted"]),
        "seeds": 5,
        "output_csv": "wikics_sar_sampling_nnif_batch_cluster.csv",
        "min":0.88,
        "clusters":trial.suggest_categorical("clusters", [50,100,200,300,400]),          
        "num_epochs":100,         
        "sampling":trial.suggest_categorical("sampling",["sage","cluster","shine"]),         
        
       
    }
    
    avg_f1, std_f1 = run_nnif_gnn_experiment(params)
    
    # We aim to maximize F1 score.
    return avg_f1

# Create an Optuna study to maximize the F1 score.
study = optuna.create_study(direction="maximize")
study.optimize(objective, n_trials=200)

# Print out the best hyperparameters and corresponding F1 score.
print("Best trial:")
trial = study.best_trial
print("  Average F1:", trial.value)
print("  Best parameters:")
for key, value in trial.params.items():
    print(f"    {key}: {value}")


# Elliptic Bitcoin

In [1]:
from train_NNIF_GNN import run_nnif_gnn_experiment
import optuna
from typing import Dict, Any

def objective(trial: optuna.trial.Trial) -> float:
    """
    Objective function for hyperparameter optimization using Optuna.
    It builds a parameter dictionary, calls the experiment function, and
    returns the average F1 score.
    """
    params: Dict[str, Any] = {
        "dataset_name": "elliptic-bitcoin",      
        "mechanism": "SAR2",
        "train_pct": 0.5,
        "alpha": 0.5,
        "K": trial.suggest_int("K", 2, 20),
        "layers": trial.suggest_int("layers", 1, 2),
        "hidden_channels": trial.suggest_categorical("hidden_channels", [64,128, 256]),
        "out_channels": trial.suggest_categorical("out_channels", [64,128, 256]),
        "norm": None,
        "dropout": trial.suggest_float("dropout", 0, 0.4),
        "ratio": trial.suggest_float("ratio", 0.001, 0.03),
        "aggregation": 'mean',
        "treatment": "removal",#trial.suggest_categorical("treatment", ["removal", "relabeling"]),
        "model_type": trial.suggest_categorical("model_type", ['GCNConv', 'GATConv']),
        "rate_pairs":trial.suggest_int("rate_pairs",1,15),
        "batch_size": trial.suggest_categorical("batch_size", [5,10,15,20]),
        "lr": trial.suggest_float("lr", 1e-4, 1e-2),
        "anomaly_detector":"nearest_neighbors",#trial.suggest_categorical("anomaly_detector",["nearest_neighbors","unweighted"]),
        "seeds": 1,
        "output_csv": "elliptic_bitcoin_cluster.csv",
        "min":0.65,
        "clusters":trial.suggest_categorical("clusters", [100,500,1000]),          
        "num_epochs":100,#trial.suggest_categorical("num_epochs", [50,100,150]),         
        "sampling":"cluster",#trial.suggest_categorical("sampling",["neighbor","cluster"]),         
        }

    
    # Call the experiment function with these parameters.
    # run_nnif_gnn_experiment returns (avg_f1, std_f1)
    avg_f1, std_f1 = run_nnif_gnn_experiment(params)
    
    # We aim to maximize F1 score.
    return avg_f1

# Create an Optuna study to maximize the F1 score.
study = optuna.create_study(direction="maximize")
study.optimize(objective, n_trials=200)

# Print out the best hyperparameters and corresponding F1 score.
print("Best trial:")
trial = study.best_trial
print("  Average F1:", trial.value)
print("  Best parameters:")
for key, value in trial.params.items():
    print(f"    {key}: {value}")


[I 2025-04-04 10:31:12,718] A new study created in memory with name: no-name-1f8e694f-776b-45ff-92be-1b1c7abb1f96


Running experiment with seed=654:
 - K=16, layers=2, hidden=128, out=64
 - norm=None, dropout=0.042811745845246656, batch_size=20, methodology=ours
 - ratio=0.014408704706040928, aggregation=mean, treatment=removal, anomaly_detector=nearest_neighbors, sampling=cluster
 - model_type=GCNConv, rate_pairs=13, clusters=500, lr=0.0021337433006543764


Computing METIS partitioning...
Done!


Epoch 0 / 100, Loss: 38.8043
Epoch 10 / 100, Loss: 35.0547
Epoch 20 / 100, Loss: 28.8067
Epoch 30 / 100, Loss: 21.0404
Epoch 40 / 100, Loss: 14.7131
Epoch 50 / 100, Loss: 10.2298
Epoch 60 / 100, Loss: 7.5048
Epoch 70 / 100, Loss: 5.7055
Epoch 80 / 100, Loss: 4.2609
Epoch 90 / 100, Loss: 3.3113


[I 2025-04-04 10:42:04,920] Trial 0 finished with value: 0.6484468737501666 and parameters: {'K': 16, 'layers': 2, 'hidden_channels': 128, 'out_channels': 64, 'dropout': 0.042811745845246656, 'ratio': 0.014408704706040928, 'model_type': 'GCNConv', 'rate_pairs': 13, 'batch_size': 20, 'lr': 0.0021337433006543764, 'clusters': 500}. Best is trial 0 with value: 0.6484468737501666.


...

Error: Labels must be in {0,1}, got [0].
Done. Results written to elliptic-bitcoin_experimentations\elliptic_bitcoin_cluster_0504152508.csv.
Average F1 over valid seeds: 0.0000 ± 0.0000
Running experiment with seed=654:
 - K=4, layers=1, hidden=128, out=128
 - norm=None, dropout=0.027456769022691726, batch_size=20, methodology=ours
 - ratio=0.016695805654684717, aggregation=mean, treatment=removal, anomaly_detector=nearest_neighbors, sampling=cluster
 - model_type=GCNConv, rate_pairs=6, clusters=500, lr=0.0024836631205545495


Computing METIS partitioning...
Done!


Epoch 0 / 100, Loss: 30.4772
Epoch 10 / 100, Loss: 19.1925
Epoch 20 / 100, Loss: 11.6362
Epoch 30 / 100, Loss: 7.9682
Epoch 40 / 100, Loss: 5.4701
Epoch 50 / 100, Loss: 4.0614
Epoch 60 / 100, Loss: 3.0453
Epoch 70 / 100, Loss: 2.3516
Epoch 80 / 100, Loss: 1.9151
Epoch 90 / 100, Loss: 1.4996


[I 2025-04-05 15:35:05,365] Trial 199 finished with value: 0.712346817762551 and parameters: {'K': 4, 'layers': 1, 'hidden_channels': 128, 'out_channels': 128, 'dropout': 0.027456769022691726, 'ratio': 0.016695805654684717, 'model_type': 'GCNConv', 'rate_pairs': 6, 'batch_size': 20, 'lr': 0.0024836631205545495, 'clusters': 500}. Best is trial 165 with value: 0.7249539836970813.


 - Metrics: Accuracy=0.9531, F1=0.7123, Recall=0.5947, Precision=0.8880
Done. Results written to elliptic-bitcoin_experimentations\elliptic_bitcoin_cluster_0504152543.csv.
Average F1 over valid seeds: 0.7123 ± 0.0000
Best trial:
  Average F1: 0.7249539836970813
  Best parameters:
    K: 4
    layers: 1
    hidden_channels: 128
    out_channels: 128
    dropout: 0.04553314815786919
    ratio: 0.01896077000764923
    model_type: GCNConv
    rate_pairs: 6
    batch_size: 20
    lr: 0.0033245734871396367
    clusters: 500
